# Warum ist es wichtig Elon Musk Tweets zu generieren?
Elon Musk ist seit 2020 der reichste Mann der Welt. Zusätzlich ist er eine der einflussreichsten Personen auf der Plattform und baut diesen Einfluss damit aus, dass der seit 2022 der größte Anteilseigner der Plattform ist. Bei den Theman Unternehmensanteile, Elon Musk und Twitter wird es auch abseits von Elon Musks persönlicher Finanzlage interessant. Musk ist bekannt dafür, in den letzten Jahren mit seinen Tweets Aktienkurse beeinflusst zu haben. Er hat beispielsweise 2002....
Wer finanzielle Interessen hat, könnte sich davon ausgehen damit beschäftigen, ein System zu entwickeln, das anhand von Elon Musks Meinung Aktien und Optionen kauft.
Wer finanzielle Interessen hat, sollte sich aber vielleicht auch nicht mit Elon Musks Tweets beschäftigen und denken, dass er anhand dessen der nächste Warren Buffet wird, sondern arbeiten. Viel interessanter wäre es doch eigene Tweets zu generieren. Einen Wert für die Gesellschaft hat das nicht. Damit lässt sich dennoch eine interessante Beobachtung machen. Textinhalte bei Twitter sind auf 240 Zeichen begrenzt. Komplexe Zusammenhänge mit verschiedenen Aussagen in einzelnen Tweets sind dadurch nur begrenz möglich. Die meisten Sprachmodelle haben auch genau damit ein Problem, lange zusammenhängende Texte zu generieren in denen verschiedene Aussagen koherent sind.
Die Idee Tweets mit einem Sprachmodell zu generieren ist also eigentlich sehr naheliegend und dies auch nicht der erste Ansatz. Diese fokussieren sich aber alle auf Twitter im Allgemeinen und nicht spezifisch auf das Profil eines Nutzers oder eine Nutzerin. Das Interessante an einem einzelnen Profil, ist dass die Sprache und die Gedanken eines einzelnen Menschen nachgestellt werden und nicht einer ganzen Gruppe. Genau ein Mensch nicht wie alle Menschen auf Twitter spricht soll das Model auch nicht lernen wie alle Menschen sondern eben nur wie ein Mensch zu sprechen.

In [47]:
import re

import numpy as np
import pandas as pd
import tensorflow as tf
from sklearn.model_selection import train_test_split
import os
import torch
import datasets
from transformers import DefaultDataCollator, pipeline, AutoTokenizer, AutoModelForCausalLM, TFGPT2LMHeadModel, AdamWeightDecay, TFAutoModelForCausalLM

## Daten vorbereiten

Zur Datenbeschaffung lässt sich theoretisch die API von Twitter nutzen, allerdings gibt es einen Kaggle-Datensatz, in dem die Tweets der API bereits aufbereitet sind. Der Datensatz enthält zweets von 2010 bis 2022 in einzelnen Dateien. Alle dateien werden eingelesen und in einen DataFrame zusammengefasst.

In [48]:
tweets_from_years = {}

In [49]:
for i in os.listdir('musktweets'):
    year = i.rstrip('.csv')
    print(i)
    if i == '2021.csv' or i == '2022.csv':
        tweets_from_years[year] = pd.read_csv('musktweets/'+i)
    else:
        tweets_from_years[year] = pd.read_csv('musktweets/'+i, index_col='index')

2020.csv
2021.csv
2022.csv
2019.csv
2018.csv
2015.csv
2014.csv
2016.csv
2017.csv
2013.csv
2012.csv
2010.csv
2011.csv


In [50]:
sorted(tweets_from_years['2020'].columns)

['cashtags',
 'conversation_id',
 'created_at',
 'date',
 'day',
 'geo',
 'hashtags',
 'hour',
 'id',
 'language',
 'link',
 'name',
 'near',
 'nlikes',
 'nreplies',
 'nretweets',
 'photos',
 'place',
 'quote_url',
 'reply_to',
 'retweet',
 'retweet_date',
 'retweet_id',
 'search',
 'source',
 'thumbnail',
 'timezone',
 'trans_dest',
 'trans_src',
 'translate',
 'tweet',
 'urls',
 'user_id',
 'user_id_str',
 'user_rt',
 'user_rt_id',
 'username',
 'video']

Die Tabellen ab 2020 haben ein leicht verändertes Schema und müssen an die anderen angepasst werden. Außerdem werden nur bestimmte Felder zu weiteren Arbeit genutzt.

In [51]:
for year in tweets_from_years:
    if year == '2022' or year == '2021' or year == '2020':
        tweets_from_years[year].rename(columns={'likes_count':'nlikes'}, inplace=True)
        print(tweets_from_years[year].columns)

Index(['id', 'conversation_id', 'created_at', 'date', 'timezone', 'place',
       'tweet', 'language', 'hashtags', 'cashtags', 'user_id', 'user_id_str',
       'username', 'name', 'day', 'hour', 'link', 'urls', 'photos', 'video',
       'thumbnail', 'retweet', 'nlikes', 'nreplies', 'nretweets', 'quote_url',
       'search', 'near', 'geo', 'source', 'user_rt_id', 'user_rt',
       'retweet_id', 'reply_to', 'retweet_date', 'translate', 'trans_src',
       'trans_dest'],
      dtype='object')
Index(['id', 'conversation_id', 'created_at', 'date', 'time', 'timezone',
       'user_id', 'username', 'name', 'place', 'tweet', 'language', 'mentions',
       'urls', 'photos', 'replies_count', 'retweets_count', 'nlikes',
       'hashtags', 'cashtags', 'link', 'retweet', 'quote_url', 'video',
       'thumbnail', 'near', 'geo', 'source', 'user_rt_id', 'user_rt',
       'retweet_id', 'reply_to', 'retweet_date', 'translate', 'trans_src',
       'trans_dest'],
      dtype='object')
Index(['id', 'conver

In [52]:
tweets_from_years['2021']

id      conversation_id  \
0     1476662222617251846  1476620230692679680   
1     1476656306610216960  1476644467578859528   
2     1476651519986614281  1476252898115964928   
3     1476619907076923398  1476252898115964928   
4     1476618021024190474  1476252898115964928   
...                   ...                  ...   
3110  1345384139969552389  1345382294966571008   
3111  1345382294966571008  1345382294966571008   
3112  1345344958710992897  1345334831719337984   
3113  1345208391958888448  1344675033231237120   
3114  1344810193952014336  1344518758707113986   

                                     created_at        date      time  \
0     2021-12-31 01:11:23 Arabian Standard Time  2021-12-31  01:11:23   
1     2021-12-31 00:47:53 Arabian Standard Time  2021-12-31  00:47:53   
2     2021-12-31 00:28:51 Arabian Standard Time  2021-12-31  00:28:51   
3     2021-12-30 22:23:14 Arabian Standard Time  2021-12-30  22:23:14   
4     2021-12-30 22:15:45 Arabian Standard Time  2021-12-30  22:15:45   
...                                         ...         ...       ...   
3110  2021-01-02 18:59:09 Arabian Standard Time  2021-01-02  18:59:09   
3111  2021-01-02 18:51:49 Arabian Standard Time  2021-01-02  18:51:49   
3112  2021-01-02 16:23:28 Arabian Standard Time  2021-01-02  16:23:28   
3113  2021-01-02 07:20:48 Arabian Standard Time  2021-01-02  07:20:48   
3114  2021-01-01 04:58:30 Arabian Standard Time  2021-01-01  04:58:30   

      timezone   user_id  username       name  place  ... geo source  \
0          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
1          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
2          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
4          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
...        ...       ...       ...        ...    ...  ...  ..    ...   
3110       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3111       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3112       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3113       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3114       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   

     user_rt_id user_rt retweet_id  \
0           NaN     NaN        NaN   
1           NaN     NaN        NaN   
2           NaN     NaN        NaN   
3           NaN     NaN        NaN   
4           NaN     NaN        NaN   
...         ...     ...        ...   
3110        NaN     NaN        NaN   
3111        NaN     NaN        NaN   
3112        NaN     NaN        NaN   
3113        NaN     NaN        NaN   
3114        NaN     NaN        NaN   

                                               reply_to  retweet_date  \
0     [{'screen_name': 'roshanpateI', 'name': 'Rosha...           NaN   
1     [{'screen_name': 'tesla_raj', 'name': 'Tesla R...           NaN   
2     [{'screen_name': 'CSmithson80', 'name': 'Chris...           NaN   
3     [{'screen_name': 'BLKMDL3', 'name': 'Zack', 'i...           NaN   
4     [{'screen_name': 'mims', 'name': 'Christopher ...           NaN   
...                                                 ...           ...   
3110  [{'screen_name': 'flcnhvy', 'name': 'Viv ✶', '...           NaN   
3111                                                 []           NaN   
3112  [{'screen_name': 'newscientist', 'name': 'New ...           NaN   
3113  [{'screen_name': 'comma_ai', 'name': 'comma', ...           NaN   
3114  [{'screen_name': 'PPathole', 'name': 'Pranay P...           NaN   

      translate trans_src trans_dest  
0           NaN       NaN        NaN  
1           NaN       NaN        NaN  
2           NaN       NaN        NaN  
3           NaN       NaN        NaN  
4           NaN       NaN        NaN  
...         ...       ...        ...  
3110        NaN       NaN        NaN  
3111        NaN       NaN        N

In [53]:
for year in tweets_from_years:
    print(year)
    tweets_from_years[year] = tweets_from_years[year][['nlikes','date', 'link','photos','reply_to','retweet','source','tweet','video']]


2020
2021
2022
2019
2018
2015
2014
2016
2017
2013
2012
2010
2011


In [54]:
tweets_from_years["2020"][tweets_from_years["2020"]['retweet']==True]

Empty DataFrame
Columns: [nlikes, date, link, photos, reply_to, retweet, source, tweet, video]
Index: []

In [55]:
tweets_from_all_years = pd.concat([tweets_from_years[year] for year in tweets_from_years.keys()])
tweets_from_all_years = tweets_from_all_years.reset_index()

In [56]:
tweets_from_all_years

index  nlikes                 date  \
0          0   55085  2020-12-28 19:46:18   
1          1    8631  2020-12-28 18:07:33   
2          2   72434  2020-12-28 17:23:51   
3          3   33830  2020-12-28 17:23:31   
4          4    2394  2020-12-28 05:39:42   
...      ...     ...                  ...   
34873     22      53  2011-12-03 08:22:07   
34874     23      29  2011-12-03 08:20:28   
34875     24      78  2011-12-01 10:29:04   
34876     25     189  2011-12-01 09:55:11   
34877     26    4652  2010-06-04 18:31:57   

                                                    link  \
0      https://twitter.com/elonmusk/status/1343644462...   
1      https://twitter.com/elonmusk/status/1343619610...   
2      https://twitter.com/elonmusk/status/1343608616...   
3      https://twitter.com/elonmusk/status/1343608530...   
4      https://twitter.com/elonmusk/status/1343431408...   
...                                                  ...   
34873  https://twitter.com/elonmusk/status/1428812840...   
34874  https://twitter.com/elonmusk/status/1428808713...   
34875  https://twitter.com/elonmusk/status/1421884581...   
34876  https://twitter.com/elonmusk/status/1421799282...   
34877    https://twitter.com/elonmusk/status/15434727182   

                                                  photos  \
0                                                     []   
1                                                     []   
2                                                     []   
3                                                     []   
4                                                     []   
...                                                  ...   
34873                                                 []   
34874                                                 []   
34875                                                 []   
34876  ['https://pbs.twimg.com/media/Afkf5DMCAAEJGFr....   
34877                                                 []   

                                                reply_to  retweet  source  \
0                                                     []    False     NaN   
1      [{'screen_name': 'kimpaquette', 'name': 'Kim P...    False     NaN   
2      [{'screen_name': 'richierichhhhh_', 'name': 'R...    False     NaN   
3                                                     []    False     NaN   
4      [{'screen_name': 'PPathole', 'name': 'Pranay P...    False     NaN   
...                                                  ...      ...     ...   
34873                                                 []    False     NaN   
34874                                                 []    False     NaN   
34875                                                 []    False     NaN   
34876                                                 []    False     NaN   
34877                                                 []    False     NaN   

                                                   tweet  video  
0      Entertainment will be critical when cars drive...      0  
1      @kimpaquette Just meeting with Larry Ellison t...      0  
2                            @richierichhhhh_ Absolutely      0  
3      What should Tesla do with in-car gaming in an ...      0  
4                              @PPathole @WSJ Absolutely      0  
...                                                  ...    ...  
34873                  That was a total non sequitur btw      0  
34874  Great Voltaire quote, arguably better than Twa...      0  
34875  I made the volume on the Model S  http://t.co/...      0  
34876  Went to Iceland on Sat to ride bumper cars on ...      1  
34877  Please ignore prior tweets, as that was someon...      0  

[34878 rows x 10 columns]

In den X Tweets gibt es X Antworten auf Tweets von anderen NutzerInnen. In der Wortwahl sind Antworten aber anders als eigenständige Tweets, zudem sind Antworten ohne den ursprünglichen Tweet ziemlich nutzlos. Die automatische Generierung von Antworten wäre aber ein interessantes separates Projekt. In diesem Projekt werden aber nur eigenständige Tweets generiert, weshalb Tweets, die Antworten auf andere Tweets sind entfernt werden.

In [57]:
tweets_from_all_years = tweets_from_all_years[(tweets_from_all_years['reply_to']=='[]') & (tweets_from_all_years['retweet']==False)]

In [58]:
tweets_from_all_years[(tweets_from_all_years['retweet']!=False)].shape

(0, 10)

In [59]:
tweets_from_all_years

index  nlikes                 date  \
0          0   55085  2020-12-28 19:46:18   
3          3   33830  2020-12-28 17:23:31   
6          6  148037  2020-12-27 22:18:58   
34        34  187368  2020-12-25 20:54:29   
35        35  236833  2020-12-25 16:47:04   
...      ...     ...                  ...   
34873     22      53  2011-12-03 08:22:07   
34874     23      29  2011-12-03 08:20:28   
34875     24      78  2011-12-01 10:29:04   
34876     25     189  2011-12-01 09:55:11   
34877     26    4652  2010-06-04 18:31:57   

                                                    link  \
0      https://twitter.com/elonmusk/status/1343644462...   
3      https://twitter.com/elonmusk/status/1343608530...   
6      https://twitter.com/elonmusk/status/1343320495...   
34     https://twitter.com/elonmusk/status/1342574459...   
35     https://twitter.com/elonmusk/status/1342512194...   
...                                                  ...   
34873  https://twitter.com/elonmusk/status/1428812840...   
34874  https://twitter.com/elonmusk/status/1428808713...   
34875  https://twitter.com/elonmusk/status/1421884581...   
34876  https://twitter.com/elonmusk/status/1421799282...   
34877    https://twitter.com/elonmusk/status/15434727182   

                                                  photos reply_to  retweet  \
0                                                     []       []    False   
3                                                     []       []    False   
6                                                     []       []    False   
34                                                    []       []    False   
35     ['https://pbs.twimg.com/media/EqGPuYCUwAIb7_U....       []    False   
...                                                  ...      ...      ...   
34873                                                 []       []    False   
34874                                                 []       []    False   
34875                                                 []       []    False   
34876  ['https://pbs.twimg.com/media/Afkf5DMCAAEJGFr....       []    False   
34877                                                 []       []    False   

       source                                              tweet  video  
0         NaN  Entertainment will be critical when cars drive...      0  
3         NaN  What should Tesla do with in-car gaming in an ...      0  
6         NaN  Try playing Polytopia in your Tesla! Great gam...      0  
34        NaN  Change your horn sound to 🐐, 🐍🎷, 💨 or holiday ...      0  
35        NaN  Merry Christmas &amp; happy holidays! 🎁  https...      1  
...       ...                                                ...    ...  
34873     NaN                  That was a total non sequitur btw      0  
34874     NaN  Great Voltaire quote, arguably better than Twa...      0  
34875     NaN  I made the volume on the Model S  http://t.co/...      0  
34876     NaN  Went to Iceland on Sat to ride bumper cars on ...      1  
34877     NaN  Please ignore prior tweets, as that was someon...      0  

[16413 rows x 10 columns]

Für das Training werden außerdem Links durch einen Link Tag '<link>' ersetzt, weil mit einem Modell natürlich keine echten Links generiert werden können.

In [60]:
url_re = re.compile(r"https?:\/\/\S*")
tweets_from_all_years['tweet']=tweets_from_all_years.apply(lambda x: url_re.sub('<link>',x['tweet'] if x['video'] == 0 else url_re.sub('<image>',x['tweet'])), axis=1)

/var/folders/w_/ycxlqjsx2yj7n7qz4rl_dcnm0000gn/T/ipykernel_4755/2591080739.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tweets_from_all_years['tweet']=tweets_from_all_years.apply(lambda x: url_re.sub('<link>',x['tweet'] if x['video'] == 0 else url_re.sub('<image>',x['tweet'])), axis=1)


In [61]:
tweets_from_all_years

index  nlikes                 date  \
0          0   55085  2020-12-28 19:46:18   
3          3   33830  2020-12-28 17:23:31   
6          6  148037  2020-12-27 22:18:58   
34        34  187368  2020-12-25 20:54:29   
35        35  236833  2020-12-25 16:47:04   
...      ...     ...                  ...   
34873     22      53  2011-12-03 08:22:07   
34874     23      29  2011-12-03 08:20:28   
34875     24      78  2011-12-01 10:29:04   
34876     25     189  2011-12-01 09:55:11   
34877     26    4652  2010-06-04 18:31:57   

                                                    link  \
0      https://twitter.com/elonmusk/status/1343644462...   
3      https://twitter.com/elonmusk/status/1343608530...   
6      https://twitter.com/elonmusk/status/1343320495...   
34     https://twitter.com/elonmusk/status/1342574459...   
35     https://twitter.com/elonmusk/status/1342512194...   
...                                                  ...   
34873  https://twitter.com/elonmusk/status/1428812840...   
34874  https://twitter.com/elonmusk/status/1428808713...   
34875  https://twitter.com/elonmusk/status/1421884581...   
34876  https://twitter.com/elonmusk/status/1421799282...   
34877    https://twitter.com/elonmusk/status/15434727182   

                                                  photos reply_to  retweet  \
0                                                     []       []    False   
3                                                     []       []    False   
6                                                     []       []    False   
34                                                    []       []    False   
35     ['https://pbs.twimg.com/media/EqGPuYCUwAIb7_U....       []    False   
...                                                  ...      ...      ...   
34873                                                 []       []    False   
34874                                                 []       []    False   
34875                                                 []       []    False   
34876  ['https://pbs.twimg.com/media/Afkf5DMCAAEJGFr....       []    False   
34877                                                 []       []    False   

       source                                              tweet  video  
0         NaN  Entertainment will be critical when cars drive...      0  
3         NaN  What should Tesla do with in-car gaming in an ...      0  
6         NaN  Try playing Polytopia in your Tesla! Great gam...      0  
34        NaN  Change your horn sound to 🐐, 🐍🎷, 💨 or holiday ...      0  
35        NaN   Merry Christmas &amp; happy holidays! 🎁  <image>      1  
...       ...                                                ...    ...  
34873     NaN                  That was a total non sequitur btw      0  
34874     NaN  Great Voltaire quote, arguably better than Twa...      0  
34875     NaN  I made the volume on the Model S  <link> go to...      0  
34876     NaN  Went to Iceland on Sat to ride bumper cars on ...      1  
34877     NaN  Please ignore prior tweets, as that was someon...      0  

[16413 rows x 10 columns]

Zur Generierung von natürlicher Sprache gibt es viele Optionen, eine klassische Methode ist zum Beispiel die Nutzung von Markov-Ketten.

Der moderne Ansatz sind auf neuronalen Netzen aufbauende Modelle. Einfache Perceptrons bieten aber nur wenige bis keine Möglichkeiten zusammenhängende Sätze zu verarbeiten. Stattdessen wurden Architekturen wie Recurrent Neural Networks entwickelt, in denen Neuronen auch mit Ausgaben folgender Neuronen gefüttert werden. Das LSTM speichert Eingaben vorheriger Eingaben und kann so mit sequentiellen Daten arbeiten. Der heutige Standard sind aber sogenannte Transformer. Ihre Grundlage ist der Attention-Mechanismus. Attention beruht auf Lookup-Tabellen, die im Netzwerk anlernbar sind. Beim Vorhersagen eines Elements in einer Sequenz kann also auch gelernt werden, welche Elemente davor und danach vorkommen. Das Training ist dafür sehr aufwändigt und benätigt einen sehr großen Korpus. Ein Modell, das mit einem solchen Korpus trainiert wurde ist GPT2. Der Korpus besteht aus den Texten von 8 Millionen Websites, auf die von der Internet-Plattform Reddit verlinkt wird. Weil die generierten Texte dadurch sehr gut Texte widerspiegeln, die im Internet zu finden sind, wird GPT-2 sehr oft für die Generierung von Texten, die Sprache im Intenet imitieren sollen genutzt.

In [63]:
gen = pipeline('text-generation', model='gpt2')

In [1]:
gen("Elon Musk is a ")

NameError: name 'gen' is not defined

In diesem Modell ist aber die Sprache von Elon Musk nicht gut repräsentiert. Um das zu verbessern wird auf Transfer-Learning zurückgegriffen. Beim Transfer Learning wird statt ein neues Modell zu trainieren ein existierendes Modell wie GPT-2 mit den spezifischen Daten trainiert. Die Bibliothek `transformers` bietet dafür eine Reihe von existierienden Modellen, darunter auch GTP-2 an.
Sprachemodelle können nicht mit den Rohen sprachdaten trainiert werden. Sie werden mit einer aneinanderreihung von Tokens, also numerischen Werten, die die einzelnen Wörter repräsentieren trainiert. GPT-2 bietet bereits einen passenden Tokenizer, der auf Texte mit Elon Musks Tweets angepasst werden muss. Weil das Modell immer ein Prompt braucht im Text zu generieren, wird ein `BOS_TOKEN` hinzugefügt, der als Prompt auch im Training vor jedem Tweet eingefügt wird. So lernt das Modell, dass jedem Prompt, ein Tweet von Elon Musk folgt. Es gibt auch einen End of Sequence Token, damit soll unter anderem gelernt werden, keine zu langen Texte zu generieren. In der Praxis funktioniert dies aber nur bedingt zuverlässig. Der `IMAGE_TOKEN` und der `LINK_TOKEN` sollen dafür sorgen, dass diese Teile des textes nicht aus anderne Tokens zusammengesetzt werden sondern immer am Stück vorhergesagt werden.

In [64]:
BOS_TOKEN = "<|elontext|>"
EOS_TOKEN = "<|endoftext|>"
PAD_TOKEN = "<|pad|>"
IMAGE_TOKEN = "<image>"
LINK_TOKEN = "<link>"
MAX_TOKENS = 512

In [65]:

tokenizer = AutoTokenizer.from_pretrained("gpt2",
    bos_token=BOS_TOKEN,
    eos_token=EOS_TOKEN,
    pad_token=PAD_TOKEN,
    max_length=MAX_TOKENS,
    is_split_into_words=True,
)
#tokenizer.add_tokens([LINK_TOKEN, IMAGE_TOKEN])

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [66]:
distil_tokenizer = AutoTokenizer.from_pretrained("distilgpt2",
                                          bos_token=BOS_TOKEN,
                                          eos_token=EOS_TOKEN,
                                          pad_token=PAD_TOKEN,
                                          max_length=MAX_TOKENS,
                                          is_split_into_words=True,
                                          )
distil_tokenizer.add_tokens([LINK_TOKEN, IMAGE_TOKEN])

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


2

Neben GPT-2 wird ausßerdem noch das Modell 'distil-gpt2' genutzt. Das ist eine kleinere Version von 'GPT-2' und nutzt etwa die Hälfte der Neuronen bzw. Parameter. Beide Modelle sollen verglichen werden.

Um sicher zu gehen, dass mit korrekten Daten gelernt wird, werden die Tokenizer einmal getestet. Dafür wird ein Text encodiert und decodiert. Dann wird geprüft, ob der noch lesbar ist.

In [67]:
some_tweets = tweets_from_all_years.sample(n=10, random_state=30)
encoded = tokenizer(some_tweets['tweet'].to_list()[0], padding=True, max_length=MAX_TOKENS, pad_to_max_length=True,)
decoded = tokenizer.decode(encoded['input_ids'])
some_tokens=[]
for i in some_tweets['tweet']:
    some_tokens.append(' '.join(i.split(' ')[:5]))


/usr/local/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2301: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/usr/local/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2306: UserWarning: Though `pad_to_max_length` = `True`, it is ignored because `padding`=`True`.
  warnings.warn("Though `pad_to_max_length` = `True`, it is ignored because `padding`=`True`.")


In [ ]:
encoded = tokenizer(some_tweets['tweet'].to_list()[0], padding=True, max_length=MAX_TOKENS, pad_to_max_length=True,)
decoded = tokenizer.decode(encoded['input_ids'])
some_distil_tokens=[]
for i in some_tweets['tweet']:
    some_distil_tokens.append(' '.join(i.split(' ')[:5]))

In [68]:
some_tokens

['3 mins to liftoff',
 "Congratulations to @OrbitalSciences! “@CNETNews: Orbital's",
 'Noodles in Shinjuku  <image>',
 'Starlink has been told by',
 'Drone spaceport ship heads to',
 'Excited about the Tesla Autopilot',
 'Rocket engines are healthy, but',
 'Preparing to launch a Thaicom',
 "Can't make this stuff up:",
 'First will rewatch Godfather Part']

Die Erstellung von Datensätzen, die mit Tensorflow und dem Modell kompatibel sind ist eine größere Herausforderung. Dafür wird die `transformers` zugehörige Bibliothek `datasets` verwendet. Außerdem wird ein Train-und Test-Split erstellt. Das Test Split wird zum Hyperparameter-Tuning und Testing verwendet.

In [76]:
## Set tweets to subset or to full dataset
#tweet_ds = some_tweets
import datasets
tweet_ds = tweets_from_all_years
# Damit sich der Datensatz nachher sicher in das Tensorflow Datenformat konvertieren lässt muss mit dem Datenset-Format der transformers library erstellt werden
tweets_ds = datasets.Dataset.from_pandas(tweet_ds[['tweet']])

tweets_ds = tweets_ds.train_test_split(test_size=0.2)
MAX_TOKENS = max([len(tokenizer.encode(tweet, add_special_tokens=True)) for tweet in tweet_ds['tweet']])+2
DISTIL_MAX_TOKENS = max([len(distil_tokenizer.encode(tweet, add_special_tokens=True)) for tweet in tweet_ds['tweet']])+2

In [77]:
tweets_ds['train']

Dataset({
    features: ['tweet', '__index_level_0__'],
    num_rows: 13130
})

Die `prepare_text` Funktion wird später mit einer `map` Funktion verwendet um die Texte in token-sequenzen umzuwandeln.

In [78]:
## mit anpassungen übernommen aus https://data-dive.com/finetune-german-gpt2-on-tpu-transformers-tensorflow-for-text-generation-of-reviews
def prepare_text(tweets:list, prep_tokenizer, prep_MAX_TOKENS):
    # Einfügen der Prompts vor jeden Tweet
    text = [BOS_TOKEN + tweet + EOS_TOKEN for tweet in tweets['tweet']]

    tokenized = prep_tokenizer(
        text,
        add_special_tokens=True,  # Only adds pad not eos and bos
        max_length=prep_MAX_TOKENS,
        truncation=True,
        pad_to_max_length=True,
    )
    tokenized["labels"] = tokenized["input_ids"].copy()
    #tokenized["labels"] = [x[1:] for x in tokenized["input_ids"]]
    #tokenized["labels"] = [
    #[-100 if x == tokenizer.pad_token_id else x for x in y]
    #for y in tokenized["labels"]
    #    ]
    # truncate input ids and attention mask to account for label shift
    #tokenized["input_ids"] = [x[:-1] for x in tokenized["input_ids"]]
    #tokenized["attention_mask"] = [x[:-1] for x in tokenized["attention_mask"]]

    return tokenized

In [79]:
distil_tweets_ds = tweets_ds.map(
    lambda x: prepare_text(x, distil_tokenizer,DISTIL_MAX_TOKENS),
    batched=True,
    #num_proc=4,
    # ursprünglich spalten entfernen
    remove_columns=['tweet','__index_level_0__'],
    load_from_cache_file=True,
)

  0%|          | 0/14 [00:00<?, ?ba/s]

/usr/local/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2285: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


  0%|          | 0/4 [00:00<?, ?ba/s]

In [80]:
tweets_ds = tweets_ds.map(
    lambda x: prepare_text(x, tokenizer, MAX_TOKENS),
    batched=True,
    #num_proc=4,
    remove_columns=['tweet','__index_level_0__'],
    load_from_cache_file=True,
)

  0%|          | 0/14 [00:00<?, ?ba/s]

/usr/local/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2285: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


  0%|          | 0/4 [00:00<?, ?ba/s]

In [ ]:
Erstellung der Datensätze

In [83]:
train_ds = prepare_text(tweets_train['tweet'],tokenizer)
test_ds = prepare_text(tweets_test['tweet'], tokenizer)

NameError: name 'tweets_train' is not defined

Der fertige Text wird zum Test nochmal dekodiert. Nun sind auch Padding Tokens vorhanden, um alle Sequenzen auf die gleiche Länge, und damit in ein für das Modell zu verarbeitende Format zu bringen.

In [81]:
for i in tweets_ds['train']:
    print(tokenizer.decode(i['input_ids']))

<|elontext|>@_amwolo_ They can. Will be great for road trips and camping<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|>
<|elontext|>@GoesAzedo yes<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|>

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



<|elontext|>My Shiba Inu will be named Floki<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|>
<|elontext|>Buying a car in 2019 that can’t upgrade to full self-driving is like buying a horse instead of a car in 1919  <link><|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|p

Das Datenset muss in das von Tensorflow Datenformat konvertiert werden. Dieses Datenformat ist

In [84]:

def build_tf_dataset(tokenized_texts, attention_mask, labels):
    # Create tf.data.Dataset

    #datasets.Dataset.from_pandas((tokenized_texts, attention_mask, labels))

    dataset = tf.data.Dataset.from_tensor_slices(
        ({
            'input_ids':tf.convert_to_tensor(tokenized_texts,name='input_ids'),
            'attention_mask':tf.convert_to_tensor(attention_mask, name='attention_mask'),
            'labels':tf.convert_to_tensor(labels, name='labels'),
    },
        tf.convert_to_tensor(labels, name='labels')
        )
    )
    return dataset

In [85]:
train =build_tf_dataset(train_ds['input_ids'], train_ds['attention_mask'], train_ds['labels'])
test =build_tf_dataset(test_ds['input_ids'], test_ds['attention_mask'],test_ds['labels'])

NameError: name 'train_ds' is not defined

In [91]:
data_collator = DefaultDataCollator(return_tensors="tf")
BATCH_SIZE = 32

In [92]:

train = tweets_ds['train'].to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=True,
    batch_size=16,
    collate_fn=data_collator,
)
test = tweets_ds['test'].to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=False,
    batch_size=16,
    collate_fn=data_collator,
)

In [93]:
distil_train = distil_tweets_ds['train'].to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=True,
    batch_size=BATCH_SIZE,
    collate_fn=data_collator,
)
distil_test = distil_tweets_ds['test'].to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=False,
    batch_size=BATCH_SIZE,
    collate_fn=data_collator,
)

In [94]:
distil_train

<PrefetchDataset element_spec={'labels': TensorSpec(shape=(32, None), dtype=tf.int64, name=None), 'input_ids': TensorSpec(shape=(32, None), dtype=tf.int64, name=None), 'attention_mask': TensorSpec(shape=(32, None), dtype=tf.int64, name=None)}>

In [95]:
BUFFER_SIZE = len(train)
DISTIL_BUFFER_SIZE = len(distil_train)


In [96]:
distil_train_batched = distil_train.shuffle(len(distil_train)).batch(BATCH_SIZE)
distil_test_batched = distil_test.batch(BATCH_SIZE)

In [97]:
train = train.shuffle(len(train))#.batch(BATCH_SIZE)
test = test#.batch(BATCH_SIZE)
train_batched = train.batch(BATCH_SIZE)
test_batched = test.batch(BATCH_SIZE)

In [98]:

#model = AutoModelForCausalLM.from_pretrained("gpt2")
model = TFGPT2LMHeadModel.from_pretrained(
#model=TFAutoModelForCausalLM.from_pretrained(
    "gpt2",
    pad_token_id=tokenizer.pad_token_id,
    eos_token_id=tokenizer.eos_token_id,
    bos_token_id=tokenizer.bos_token_id,
)
distil_model = TFGPT2LMHeadModel.from_pretrained(
    "distilgpt2",
    pad_token_id=tokenizer.pad_token_id,
    eos_token_id=tokenizer.eos_token_id,
    bos_token_id=tokenizer.bos_token_id,
)
model.resize_token_embeddings(len(tokenizer))
distil_model.resize_token_embeddings(len(distil_tokenizer))
optimizer = AdamWeightDecay(lr=2e-5, weight_decay_rate=0.01)
distil_optimizer = AdamWeightDecay(lr=1e-6, weight_decay_rate=0.01)
model.compile(optimizer=optimizer)
distil_model.compile(optimizer=distil_optimizer)

All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at gpt2.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.
All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at distilgpt2.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.
/usr/local/lib/python3.9/site-packages/keras/optimizer_v2/adam.py:105: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)
No loss specified in compile() - the model's internal loss computation will be used as the loss. Don't panic - this is a common way to train TensorFlow mod

In [607]:
model.fit(
    train_batched,
    epochs=2,
    steps_per_epoch=BUFFER_SIZE / BATCH_SIZE,
)

Epoch 1/2
384/384 [==============================] - 16359s 43s/step - loss: 2.1567
Epoch 2/2
384/384 [==============================] - 24508s 64s/step - loss: 1.2140


In [99]:
for i in distil_train:
    print(distil_tokenizer.decode(i["labels"][0]))
    break

<|elontext|>Over 30,000 hats sold!<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|>


In [100]:
#model.save("./gpt2musktf")

KeyboardInterrupt: 

In [169]:
tokenizer.save_pretrained('./musktokenizer')

('./musktokenizer/tokenizer_config.json',
 './musktokenizer/special_tokens_map.json',
 './musktokenizer/vocab.json',
 './musktokenizer/merges.txt',
 './musktokenizer/added_tokens.json',
 './musktokenizer/tokenizer.json')

In [102]:
distil_model.fit(
    distil_train,
    epochs=3,
    steps_per_epoch= DISTIL_BUFFER_SIZE / BATCH_SIZE,
    validation_data=distil_test,
)

Epoch 1/3
12/12 [==============================] - 272s 22s/step - loss: 18.1975 - val_loss: 17.8993
Epoch 2/3
12/12 [==============================] - 278s 23s/step - loss: 16.5287 - val_loss: 17.3399
Epoch 3/3
12/12 [==============================] - 287s 24s/step - loss: 16.8257 - val_loss: 16.6095


In [217]:
#distil_model.save_pretrained("./distilmusk")

## Hyperparameter Optimierung
Hyperparameter Optimierung hat bei generativen Sprachemodellen nur einen geringen Einfluss. Ein Modell ist aufgrund schlechterer Metriken, in der Wahrnehmung eines Menschen zwangsläufig schlechter. Im Voraus lässt sich dazu allerdings kein Beurteilung machen.

In [27]:
import keras_tuner as kt

In [ ]:
#tunable parameters
batch_size=16
lr=2e-5
num_train_epochs=5

In [ ]:
#https://wandb.ai/amogkam/transformers/reports/Hyperparameter-Optimization-for-Huggingface-Transformers--VmlldzoyMTc2ODI
class Model(kt.HyperModel):

    def build(self, hp: kt.HyperParameters):
        BATCH_SIZE = hp.Choice('batch_size',[4,8,16,32])
        model = TFGPT2LMHeadModel.from_pretrained(
            #model=TFAutoModelForCausalLM.from_pretrained(
            "gpt2",
            pad_token_id=tokenizer.pad_token_id,
            eos_token_id=tokenizer.eos_token_id,
            bos_token_id=tokenizer.bos_token_id,
        )
        model.resize_token_embeddings(len(tokenizer))
        optimizer = AdamWeightDecay(lr=hp.Choice('learning_rate', [2e-5, 3e-5, 5e-5]), weight_decay_rate=hp.Choice('weight_decay_rate',[0,0.01]))
        model.compile(optimizer=optimizer)
        return model
    def fit(self, hp, model, *args, **kwargs):
        return model.fit(
            train,
            batch_size= BATCH_SIZE,
            epochs=hp.Int('epochs',min_value=2, max_value=5),
            steps_per_epoch=BUFFER_SIZE / BATCH_SIZE,
        )


In [ ]:
tuner = kt.BayesianOptimization(
    objective="val_accuracy",
    max_trials=3,
    overwrite=True,
    directory="hyper-opt/",
    project_name="tune_musk",
)

In [604]:
tokenizer.decode([])

'!'

In [3]:
## Modell inference

In [109]:
model = TFGPT2LMHeadModel.from_pretrained("./gpt2musk")

All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at ./gpt2musk.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.


In [107]:
distil_model = TFGPT2LMHeadModel.from_pretrained("./distilmusk")

All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at ./distilmusk.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.


In [110]:
gen = pipeline(
    "text-generation",
    model=model,
    tokenizer=tokenizer)

In [108]:
distil_gen= pipeline('text-generation', model=distil_model, tokenizer=distil_tokenizer)

## Evaluate Models
Ein gene

In [9]:
#default model
gen(BOS_TOKEN)

[{'generated_text': '<|elontext|>In one sense, Tesla is quite like a vacuum chamber. In a vacuum chamber, a vacuum tube is connected to a. In a vacuum air tank, a liquid oxygen tank is connected to a vacuum air chamber (or whatever).\n'}]

In [ ]:
#default model mit tweet prompt

In [115]:
# trainiertes modell
gen(BOS_TOKEN)

[{'generated_text': '<|elontext|>A real estate agent with a real estate agent background and a real estate broker background.'}]

In [ ]:
#trainiertes modell mit tweet prompt

In [116]:
#trainiertes modell mit hyperparameter tuning
gen(BOS_TOKEN)

[{'generated_text': '<|elontext|>Sawyer, @SolarCity &amp; all of SolarCity and Tesla are working together to solve the solar storm. Not everyone is ready.'}]

In [112]:
#trainiertes distilgpt2 modell mit hyperparamerter tuning
distil_gen(BOS_TOKEN)

[{'generated_text': '<|elontext|><image> was a and a person.\n<link> was a couple of weeks ago. It gave me a great idea of how this might be with the other games.'}]

In [ ]:
#trainiertes distilgpt2 modell mit hyperparamerter tuning mit tweet prompt

In [ ]:
# Loss berechnung aller gpt2 Modelle mit Tweet Prompt

In [ ]:
# Loss Berechnung aller distilgpt2 Modelle

In [35]:
TFGPT2LMHeadModel.from_pretrained('gpt2').compute_loss()

All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at gpt2.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.


TypeError: 'NoneType' object is not callable

## Auswahl eines Modells für eine Evaluierung mit Testsubjekten
Mit einer Gruppe Studierender soll evaluiert werden ob es mit dem Modell möglich ist tweets zu generieren, die von echten Tweets nicht zu unterscheiden sind, dafür soll eines der Modelle ausgewählt werden.
Weil zum Zeitpunkt des Test noch